# **Chatbot using Seq2Seq LSTM models**

# Step 1: Import all the packages 

In [1]:
import numpy as np 
import tensorflow as tf
import pickle
from tensorflow.keras import layers, activations, models, preprocessing
from tensorflow.keras import preprocessing, utils
import os
import yaml

# Step 3: Preprocessing the data

### a) Reading the data from the files
We parse each of the .yaml files.

1. Concatenate two or more sentences if the answer has two or more of them.
2. Remove unwanted data types which are produced while parsing the data.
3. Append <START> and <END> to all the answers.
4. Create a Tokenizer and load the whole vocabulary ( questions + answers ) into it.

The dataset contains .yml files which have pairs of different questions and their answers on varied subjects like history, bot profile, science etc.
We can easily read them as folows:

In [2]:
dir_path = '/kaggle/input/chatterbotenglish/'
files_list = os.listdir(dir_path + os.sep)

In [3]:
questions = list()
answers = list()

for filepath in files_list:
    stream = open( dir_path + os.sep + filepath , 'rb')
    docs = yaml.safe_load(stream)
    conversations = docs['conversations']
    for con in conversations:
        if len( con ) > 2 :
            questions.append(con[0])
            replies = con[ 1 : ]
            ans = ''
            for rep in replies:
                ans += ' ' + rep
            answers.append( ans )
        elif len( con )> 1:
            questions.append(con[0])
            answers.append(con[1])

answers_with_tags = list()
for i in range( len( answers ) ):
    if type( answers[i] ) == str:
        answers_with_tags.append( answers[i] )
    else:
        questions.pop( i )

answers = list()
for i in range( len( answers_with_tags ) ) :
    answers.append( '<START> ' + answers_with_tags[i] + ' <END>' )

tokenizer = preprocessing.text.Tokenizer()
tokenizer.fit_on_texts( questions + answers )
VOCAB_SIZE = len( tokenizer.word_index )+1
print( 'VOCAB SIZE : {}'.format( VOCAB_SIZE ))

VOCAB SIZE : 1894


### b) Preparing data for Seq2Seq model

This model requires 3 arrays encoder_input_data, decoder_input_data and decoder_output_data.

For encoder_input_data:
Tokensize the Questions and Pad them to their maximum Length.

For decoder_input_data:
Tokensize the Answers and Pad them to their maximum Length.

For decoder_output_data:
Tokensize the Answers and Remove the 1st element from all the tokenized_answers. This is the <START> element which was added earlier.

In [4]:
from gensim.models import Word2Vec
import re

In [5]:
vocab = []
for word in tokenizer.word_index:
  vocab.append(word)

def tokenize(sentences):
  tokens_list = []
  vocabulary = []
  for sentence in sentences:
    sentence = sentence.lower()
    sentence = re.sub('[^a-zA-Z]', ' ', sentence)
    tokens = sentence.split()
    vocabulary += tokens
    tokens_list.append(tokens)
  return tokens_list, vocabulary

In [6]:
#encoder_input_data
tokenized_questions = tokenizer.texts_to_sequences( questions )
maxlen_questions = max( [len(x) for x in tokenized_questions ] )
print(maxlen_questions)
padded_questions = preprocessing.sequence.pad_sequences( tokenized_questions, maxlen = maxlen_questions, padding = 'post')
encoder_input_data = np.array(padded_questions)
print(encoder_input_data.shape, maxlen_questions)

22
(564, 22) 22


In [7]:
# decoder_input_data
tokenized_answers = tokenizer.texts_to_sequences( answers )
maxlen_answers = max( [ len(x) for x in tokenized_answers ] )
print(maxlen_answers)
padded_answers = preprocessing.sequence.pad_sequences( tokenized_answers , maxlen=maxlen_answers , padding='post' )
decoder_input_data = np.array( padded_answers )
print( decoder_input_data.shape , maxlen_answers )

74
(564, 74) 74


In [8]:
# decoder_output_data
tokenized_answers = tokenizer.texts_to_sequences( answers )
for i in range(len(tokenized_answers)) :
    tokenized_answers[i] = tokenized_answers[i][1:]
padded_answers = preprocessing.sequence.pad_sequences( tokenized_answers , maxlen=maxlen_answers , padding='post' )
onehot_answers = utils.to_categorical( padded_answers , VOCAB_SIZE )
decoder_output_data = np.array( onehot_answers )
print( decoder_output_data.shape )

(564, 74, 1894)


Saving tokenizer params for reloading tokenizer during inference time

In [9]:
with open('tokenizer.pkl', 'wb') as f:
    pickle.dump(tokenizer, f)

In [10]:
with open('tokenizer_params.pkl', 'wb') as f:
    tokenizer_params = {
        'word_index': tokenizer.word_index,
        'maxlen_questions' : maxlen_questions,
        'maxlen_answers': maxlen_answers
        # Add other tokenizer attributes you might need for inference
    }
    pickle.dump(tokenizer_params, f)

Using Glove Embedding for better embeddings computation and better understanding of the context

In [11]:
glove_path = "/kaggle/input/glove-embeddings/glove.6B.100d.txt"
embedding_dim = 100

In [12]:
embeddings_index = {}
with open(glove_path, "r", encoding="utf-8") as f:
    for line in f:
        values = line.split()
        word = values[0]
        coefs = np.asarray(values[1:], dtype="float32")
        embeddings_index[word] = coefs

In [13]:
embedding_matrix = np.zeros((VOCAB_SIZE, embedding_dim))
for word, i in tokenizer.word_index.items():
    embedding_vector = embeddings_index.get(word)
    if embedding_vector is not None:
        embedding_matrix[i] = embedding_vector

# Step 4: Defining Encoder Decoder Model





In [14]:
encoder_inputs = tf.keras.layers.Input(shape=( maxlen_questions , ))
encoder_embedding = tf.keras.layers.Embedding(VOCAB_SIZE, embedding_dim, mask_zero=True, weights=[embedding_matrix], trainable=False)(encoder_inputs)
encoder_outputs , state_h , state_c = tf.keras.layers.LSTM( 200 , return_state=True )( encoder_embedding )
encoder_states = [ state_h , state_c ]

decoder_inputs = tf.keras.layers.Input(shape=( maxlen_answers ,  ))
decoder_embedding = tf.keras.layers.Embedding(VOCAB_SIZE, embedding_dim, mask_zero=True, weights=[embedding_matrix], trainable=False)(decoder_inputs)
decoder_lstm = tf.keras.layers.LSTM( 200 , return_state=True , return_sequences=True )
decoder_outputs , _ , _ = decoder_lstm ( decoder_embedding , initial_state=encoder_states )
decoder_dense = tf.keras.layers.Dense( VOCAB_SIZE , activation=tf.keras.activations.softmax ) 
output = decoder_dense ( decoder_outputs )

model = tf.keras.models.Model([encoder_inputs, decoder_inputs], output )
model.compile(optimizer=tf.keras.optimizers.RMSprop(), loss='categorical_crossentropy', metrics=['accuracy'])

model.summary()

Model: "model"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            [(None, 22)]         0                                            
__________________________________________________________________________________________________
input_2 (InputLayer)            [(None, 74)]         0                                            
__________________________________________________________________________________________________
embedding (Embedding)           (None, 22, 100)      189400      input_1[0][0]                    
__________________________________________________________________________________________________
embedding_1 (Embedding)         (None, 74, 100)      189400      input_2[0][0]                    
______________________________________________________________________________________________

# Step 5: Training the Model

We train the model for a number of epochs with RMSprop optimizer and categorical_crossentropy loss function.

In [15]:
model.fit([encoder_input_data , decoder_input_data], decoder_output_data, batch_size=50, epochs=150 ) 
model.save( 'model.h5' )

Epoch 1/150
12/12 [==============================] - 10s 37ms/step - loss: 1.2434 - accuracy: 0.0972
Epoch 2/150
12/12 [==============================] - 0s 33ms/step - loss: 1.1017 - accuracy: 0.1295
Epoch 3/150
12/12 [==============================] - 0s 35ms/step - loss: 1.0790 - accuracy: 0.1365
Epoch 4/150
12/12 [==============================] - 0s 35ms/step - loss: 1.0583 - accuracy: 0.1428
Epoch 5/150
12/12 [==============================] - 0s 34ms/step - loss: 1.0413 - accuracy: 0.1482
Epoch 6/150
12/12 [==============================] - 0s 35ms/step - loss: 1.0224 - accuracy: 0.1564
Epoch 7/150
12/12 [==============================] - 0s 35ms/step - loss: 1.0077 - accuracy: 0.1671
Epoch 8/150
12/12 [==============================] - 0s 36ms/step - loss: 0.9911 - accuracy: 0.1733
Epoch 9/150
12/12 [==============================] - 0s 35ms/step - loss: 0.9770 - accuracy: 0.1828
Epoch 10/150
12/12 [==============================] - 0s 34ms/step - loss: 0.9620 - accuracy: 0.193

# Step 6: Defining Inference Models

Encoder Inference Model: Takes questions as input and outputs LSTM states (h and c)

Decoder Inference Model: Takes in 2 inputs one are the LSTM states, second are the answer input sequences. it will o/p the answers for questions which fed to the encoder model and it's state values.

In [16]:
def make_inference_models():
    
    encoder_model = tf.keras.models.Model(encoder_inputs, encoder_states)
    encoder_model.save('encoder_model.h5')
    
    decoder_state_input_h = tf.keras.layers.Input(shape=( 200 ,))
    decoder_state_input_c = tf.keras.layers.Input(shape=( 200 ,))
    
    decoder_states_inputs = [decoder_state_input_h, decoder_state_input_c]
    
    decoder_outputs, state_h, state_c = decoder_lstm(
        decoder_embedding , initial_state=decoder_states_inputs)
    
    decoder_states = [state_h, state_c]

    decoder_outputs = decoder_dense(decoder_outputs)
    
    decoder_model = tf.keras.models.Model(
        [decoder_inputs] + decoder_states_inputs,
        [decoder_outputs] + decoder_states)
    decoder_model.save('decoder_model.h5')
    
    return encoder_model , decoder_model

In [20]:
enc_model, dec_model = make_inference_models()

# Step 7: Talking with the Chatbot

define a method str_to_tokens which converts str questions to Integer tokens with padding.

1. First, we take a question as input and predict the state values using enc_model.
2. We set the state values in the decoder's LSTM.
3. Then, we generate a sequence which contains the <start> element.
4. We input this sequence in the dec_model.
5. We replace the <start> element with the element which was predicted by the dec_model and update the state values.
6. We carry out the above steps iteratively till we hit the <end> tag or the maximum answer length.



In [21]:
def str_to_tokens( sentence : str ):

    words = sentence.lower().split()
    tokens_list = list()
  
    for word in words:
        tokens_list.append( tokenizer.word_index[ word ] ) 
    return preprocessing.sequence.pad_sequences( [tokens_list] , maxlen=maxlen_questions , padding='post')


In [22]:
tests = ['You can not move', 'You sound like Data', 'Stupid', 'you are idiot', 'i am going to die']
for i in range(5):
        states_values = enc_model.predict(str_to_tokens(tests[i]))
        empty_target_seq = np.zeros((1 , 1))
        empty_target_seq[0, 0] = tokenizer.word_index['start']
        stop_condition = False
        decoded_translation = ''

        while not stop_condition :
            dec_outputs , h , c = dec_model.predict([empty_target_seq] + states_values)
            sampled_word_index = np.argmax(dec_outputs[0, -1, :])
            sampled_word = None

            for word , index in tokenizer.word_index.items() :
                if sampled_word_index == index :
                    decoded_translation += f' {word}'
                    sampled_word = word

            if sampled_word == 'end' or len(decoded_translation.split()) > maxlen_answers:
                stop_condition = True

            empty_target_seq = np.zeros((1 , 1))  
            empty_target_seq[0 , 0] = sampled_word_index
            states_values = [h , c] 
        print(f'Human: {tests[i]}')
        print()
        decoded_translation = decoded_translation.split(' end')[0]
        print(f'Bot: {decoded_translation}')
        print('_'*100)

Human: You can not move

Bot:  i can move through a network easily assuming that i'm given the ability to that is
____________________________________________________________________________________________________
Human: You sound like Data

Bot:  yes i am inspired by commander data's artificial personality
____________________________________________________________________________________________________
Human: Stupid

Bot:  bots never never feel of why are you feeling i have feelings yes i sort of have feelings i can be programmed to act as if i do not have feelings i do not have feelings i do not have feelings i do not have feelings i do not have feelings i do not have feelings i do not have feelings i do not have feelings i do not have feelings i do not have
____________________________________________________________________________________________________
Human: you are idiot

Bot:  you are a cheat
________________________________________________________________________________